In [152]:
import requests
import re
import pandas as pd

import urllib
import re
import pandas as pd
import pymysql
import os
import tushare as ts
import datetime
import numpy as np

from pyecharts.charts import Kline, Line, Bar, Grid

## 获取数据：以601318为示例

In [153]:
import pymysql
 
db = pymysql.connect(host='localhost', port=3306,
                           charset='utf8',
                          user='root', password='lmy6571495')
cursor = db.cursor()
cursor.execute("use stockdata")
sql = "SELECT * FROM stock_601318"
try:
   cursor.execute(sql)
   results = cursor.fetchall()
except:
   print ("Error: unable to fetch data")
 
db.close()

In [154]:
df = pd.DataFrame(list(results),columns=['date', 'code', 'name', 'close', 'high', 'low', 'open',\
                '前收盘', '涨跌额', '涨跌幅', '换手率', '成交量', '成交金额'])
df

date    code  name  close   high    low   open    前收盘    涨跌额  \
0     2021-02-04  601318  中国平安  79.62  80.32  77.70  78.00  76.54   3.08   
1     2021-02-03  601318  中国平安  76.54  77.74  75.30  77.74  78.18  -1.64   
2     2021-02-02  601318  中国平安  78.18  79.45  77.95  79.28  79.27  -1.09   
3     2021-02-01  601318  中国平安  79.27  79.74  78.37  79.10  79.08   0.19   
4     2021-01-29  601318  中国平安  79.08  81.44  78.50  80.90  80.92  -1.84   
...          ...     ...   ...    ...    ...    ...    ...    ...    ...   
3390  2007-03-07  601318  中国平安  46.48  46.90  44.91  45.29  45.25   1.23   
3391  2007-03-06  601318  中国平安  45.25  46.00  43.75  44.00  44.38   0.87   
3392  2007-03-05  601318  中国平安  44.38  46.17  43.53  45.98  46.41  -2.03   
3393  2007-03-02  601318  中国平安  46.41  47.44  45.88  47.00  46.79  -0.38   
3394  2007-03-01  601318   N平安  46.79  50.97  45.80  50.00  33.80  12.99   

          涨跌幅      换手率        成交量         成交金额  
0      4.0240   1.3077  141654771  11200715086  
1     -2.0977   1.2405  134384298  10255482626  
2     -1.3750   0.9124   98836447   7742175159  
3      0.2403   0.6692   72490144   5729483192  
4     -2.2739   1.1722  126980032  10098743883  
...       ...      ...        ...          ...  
3390   2.7182   4.9994   28746378   1317764044  
3391   1.9603   5.1779   29772788   1337719318  
3392  -4.3741   7.2904   41919674   1880502808  
3393  -0.8121   7.3921   42504832   1981445189  
3394  38.4320  34.3936  197763351   9500302911  

[3395 rows x 13 columns]

## K-线作图

In [155]:
from pyecharts import options as opts
from pyecharts.charts import Kline
df_short = df.iloc[0:80,:]
x = df_short['date']
date = []
for i in x:
    date.append(i.__format__('%Y/%m/%d'))
  
op = df_short['open']
cl = df_short['close']
hi = df_short['high']
lo = df_short['low']
y=[]
for i in range(len(op)):
    a,b,c,d = op[i],cl[i],hi[i],lo[i]
    s=[a,b,c,d]
    y.append(s)
date=date[::-1]
y=y[::-1]


In [156]:
c = (
    Kline()
    .add_xaxis(date)
    .add_yaxis("kline", y)
    .set_global_opts(
        xaxis_opts=opts.AxisOpts(is_scale=True),
        yaxis_opts=opts.AxisOpts(
            is_scale=True,
            splitarea_opts=opts.SplitAreaOpts(
                is_show=True, areastyle_opts=opts.AreaStyleOpts(opacity=1)
            ),
        ),
        datazoom_opts=[opts.DataZoomOpts(type_="inside")],
        title_opts=opts.TitleOpts(title="Kline"),
    )
#     .render_notebook()
)
c.render_notebook()

## 日价作图

In [177]:
df_short = df.iloc[0:40,:]
x =df['date']
date = []
for i in x:
    date.append(i.__format__('%Y/%m/%d'))
  
op = df['open'].copy()
cl = df['close'].copy()
hi = df['high'].copy()
lo = df['low'].copy()
y=[]
for i in range(len(op)):
    a,b,c,d = op[i],cl[i],hi[i],lo[i]
    s=[a,b,c,d]
    y.append(s)
date=date[::-1]
y=y[::-1]

In [178]:
for i in range(len(op)):
    if cl[i] == 0:
        cl[i] = None

In [180]:
from pyecharts.charts import Line
c = (
    Line(init_opts=opts.InitOpts(width="960px", height="500px"))
    .add_xaxis(xaxis_data=date)
    .add_yaxis(
        series_name="Price",
        y_axis=cl,
#         areastyle_opts=opts.AreaStyleOpts(opacity=0.5),
        linestyle_opts=opts.LineStyleOpts(width=2, opacity=0.75),
        label_opts=opts.LabelOpts(is_show=False),
    )

    .set_global_opts(
        title_opts=opts.TitleOpts(
            title="Price Plot",
            subtitle="6001318",
            pos_left="center",
            pos_top="top",
        ),
        tooltip_opts=opts.TooltipOpts(trigger="axis", axis_pointer_type="cross"),
        legend_opts=opts.LegendOpts(pos_left="left"),
        datazoom_opts=[
            opts.DataZoomOpts(range_start=0, range_end=100),
            opts.DataZoomOpts(type_="inside", range_start=0, range_end=100),
        ],
        xaxis_opts=opts.AxisOpts(type_="category", boundary_gap=False),
        yaxis_opts=opts.AxisOpts(name="Price(¥)", type_="value", max_=200),
    )
    .set_series_opts(
        markarea_opts=opts.MarkAreaOpts(
            is_silent=False,
        ),
        axisline_opts=opts.AxisLineOpts(),
    )
#     .render("rainfall.html")
)


c.render_notebook()

## 均线作图

In [162]:
df = df.sort_values('date').copy()
df

date    code  name  close   high    low   open    前收盘    涨跌额  \
3394  2007-03-01  601318   N平安  46.79  50.97  45.80  50.00  33.80  12.99   
3393  2007-03-02  601318  中国平安  46.41  47.44  45.88  47.00  46.79  -0.38   
3392  2007-03-05  601318  中国平安  44.38  46.17  43.53  45.98  46.41  -2.03   
3391  2007-03-06  601318  中国平安  45.25  46.00  43.75  44.00  44.38   0.87   
3390  2007-03-07  601318  中国平安  46.48  46.90  44.91  45.29  45.25   1.23   
...          ...     ...   ...    ...    ...    ...    ...    ...    ...   
4     2021-01-29  601318  中国平安  79.08  81.44  78.50  80.90  80.92  -1.84   
3     2021-02-01  601318  中国平安  79.27  79.74  78.37  79.10  79.08   0.19   
2     2021-02-02  601318  中国平安  78.18  79.45  77.95  79.28  79.27  -1.09   
1     2021-02-03  601318  中国平安  76.54  77.74  75.30  77.74  78.18  -1.64   
0     2021-02-04  601318  中国平安  79.62  80.32  77.70  78.00  76.54   3.08   

          涨跌幅      换手率        成交量         成交金额  
3394  38.4320  34.3936  197763351   9500302911  
3393  -0.8121   7.3921   42504832   1981445189  
3392  -4.3741   7.2904   41919674   1880502808  
3391   1.9603   5.1779   29772788   1337719318  
3390   2.7182   4.9994   28746378   1317764044  
...       ...      ...        ...          ...  
4     -2.2739   1.1722  126980032  10098743883  
3      0.2403   0.6692   72490144   5729483192  
2     -1.3750   0.9124   98836447   7742175159  
1     -2.0977   1.2405  134384298  10255482626  
0      4.0240   1.3077  141654771  11200715086  

[3395 rows x 13 columns]

In [163]:

df['ma5']=df['open'].rolling(5).mean()
df['ma30']=df['open'].rolling(30).mean()
df['ma60']=df['open'].rolling(60).mean()
df['ma120']=df['open'].rolling(120).mean()


df_ma = df.dropna()
ma5 = df_ma['ma5'].copy()
ma30 = df_ma['ma30'].copy()
ma60 = df_ma['ma60'].copy()
ma120 = df_ma['ma120'].copy()
x =df_ma['date']
date = []
for i in x:
    date.append(i.__format__('%Y/%m/%d'))


In [169]:
c = (
    Line(init_opts=opts.InitOpts(width="960px", height="400px"))
    .add_xaxis(xaxis_data=date)
    .add_yaxis(
        series_name="MA5",
        y_axis=ma5,
#         areastyle_opts=opts.AreaStyleOpts(opacity=0.5),
        linestyle_opts=opts.LineStyleOpts(width=2, opacity=1),
        label_opts=opts.LabelOpts(is_show=False),
    )
    .add_yaxis(
        series_name="MA30",
        y_axis=ma30,
#         yaxis_index=1,
#         areastyle_opts=opts.AreaStyleOpts(opacity=0.5),
        linestyle_opts=opts.LineStyleOpts(width=2, opacity=1),
        label_opts=opts.LabelOpts(is_show=False),
    )
     .add_yaxis(
        series_name="MA60",
        y_axis=ma60,
#         yaxis_index=1,
#         areastyle_opts=opts.AreaStyleOpts(opacity=0.5),
        linestyle_opts=opts.LineStyleOpts(width=2, opacity=1),
        label_opts=opts.LabelOpts(is_show=False),
    )
     .add_yaxis(
        series_name="MA120",
        y_axis=ma120,
#         yaxis_index=1,
#         areastyle_opts=opts.AreaStyleOpts(opacity=0.5),
        linestyle_opts=opts.LineStyleOpts(width=2, opacity=1),
        label_opts=opts.LabelOpts(is_show=False),
    )


    .set_global_opts(
        title_opts=opts.TitleOpts(
            title="均线",
            subtitle="601318",
            pos_left="center",
            pos_top="top",
        ),
        tooltip_opts=opts.TooltipOpts(trigger="axis", axis_pointer_type="cross"),
        legend_opts=opts.LegendOpts(pos_left="left"),
        datazoom_opts=[
            opts.DataZoomOpts(range_start=0, range_end=100),
            opts.DataZoomOpts(type_="inside", range_start=0, range_end=100),
        ],
        xaxis_opts=opts.AxisOpts(type_="category", boundary_gap=False),
        yaxis_opts=opts.AxisOpts(name="Price(¥)", type_="value", max_=200),
    )
    .set_series_opts(
        markarea_opts=opts.MarkAreaOpts(
            is_silent=False,
            
            
        ),
        axisline_opts=opts.AxisLineOpts(),
    )
#     .render("rainfall.html")
)

c.render_notebook()

## 混合分析

In [208]:
x =df['date']
date = []
for i in x:
    date.append(i.__format__('%Y/%m/%d'))
  
op = df['open'].copy()
cl = df['close'].copy()
hi = df['high'].copy()
lo = df['low'].copy()
y=[]
# print(len(cl))
for i in range(len(cl)):
    s=[op[i],cl[i],hi[i],lo[i]]
#     s=[a,b,c,d]
    y.append(s)
ma5 = df['ma5'].copy()
ma30 = df['ma30'].copy()
ma120 = df['ma120'].copy()

In [209]:
y = y[2600:]
date = date[2600:]
ma5= ma5[2600:]
ma30 = ma30[2600:]
ma120 = ma120[2600:]
op = op[2600:]

In [210]:
kline = (
    Kline()
    .add_xaxis(date)
    .add_yaxis("kline", y)
    .set_global_opts(
        xaxis_opts=opts.AxisOpts(is_scale=True),
        yaxis_opts=opts.AxisOpts(
            is_scale=True,
            splitarea_opts=opts.SplitAreaOpts(
                is_show=True, areastyle_opts=opts.AreaStyleOpts(opacity=1)
            ),
        ),
        datazoom_opts=[opts.DataZoomOpts(type_="inside")],
        title_opts=opts.TitleOpts(title="Mix"),
    )
#     .render_notebook()
)
c = (
    Line(init_opts=opts.InitOpts(width="960px", height="450px"))
    .add_xaxis(xaxis_data=date)
    .add_yaxis(
        series_name="MA5",
        y_axis=ma5,
#         areastyle_opts=opts.AreaStyleOpts(opacity=0.5),
        linestyle_opts=opts.LineStyleOpts(width=3, opacity=0.5),
#         linestyle_opts=opts.LineStyleOpts(),
        label_opts=opts.LabelOpts(is_show=False),
    )
    .add_yaxis(
        series_name="MA30",
        y_axis=ma30,
#         yaxis_index=1,
#         areastyle_opts=opts.AreaStyleOpts(opacity=0.5),
        linestyle_opts=opts.LineStyleOpts(width=3, opacity=0.5),
#         linestyle_opts=opts.LineStyleOpts(),
        label_opts=opts.LabelOpts(is_show=False),
    )
    .add_yaxis(
        series_name="MA120",
        y_axis=ma120,
#         yaxis_index=1,
#         areastyle_opts=opts.AreaStyleOpts(opacity=0.5),
        linestyle_opts=opts.LineStyleOpts(width=3, opacity=0.5),
#         linestyle_opts=opts.LineStyleOpts(),
        label_opts=opts.LabelOpts(is_show=False),
    )


    .set_global_opts(
        title_opts=opts.TitleOpts(
            title="5日/30日均线",
            subtitle="601318",
            pos_left="center",
            pos_top="top",
        ),
        tooltip_opts=opts.TooltipOpts(trigger="axis", axis_pointer_type="cross"),
        legend_opts=opts.LegendOpts(pos_left="left"),
        datazoom_opts=[
            opts.DataZoomOpts(range_start=0, range_end=100),
            opts.DataZoomOpts(type_="inside", range_start=30, range_end=100),
        ],
        xaxis_opts=opts.AxisOpts(type_="category", boundary_gap=False),
        yaxis_opts=opts.AxisOpts(name="Price(¥)", type_="value", max_=200),
    )
    .set_series_opts(
        markarea_opts=opts.MarkAreaOpts(
            is_silent=False,
            
            
        ),
        axisline_opts=opts.AxisLineOpts(),
    )
#     .render("rainfall.html")
)

In [211]:
overlap_kline_line = kline.overlap(c)

In [212]:
grid_chart = Grid(
        init_opts=opts.InitOpts(
            width="1000px",
            height="600px",
            animation_opts=opts.AnimationOpts(animation=True),
        )
    )
grid_chart.add(
        overlap_kline_line,
        grid_opts=opts.GridOpts(pos_left="10%", pos_right="8%", height="80%"),
    )


grid_chart.render_notebook()


## 成交量分析

In [226]:
df

date    code  name  close   high    low   open    前收盘    涨跌额  \
3394  2007-03-01  601318   N平安  46.79  50.97  45.80  50.00  33.80  12.99   
3393  2007-03-02  601318  中国平安  46.41  47.44  45.88  47.00  46.79  -0.38   
3392  2007-03-05  601318  中国平安  44.38  46.17  43.53  45.98  46.41  -2.03   
3391  2007-03-06  601318  中国平安  45.25  46.00  43.75  44.00  44.38   0.87   
3390  2007-03-07  601318  中国平安  46.48  46.90  44.91  45.29  45.25   1.23   
...          ...     ...   ...    ...    ...    ...    ...    ...    ...   
4     2021-01-29  601318  中国平安  79.08  81.44  78.50  80.90  80.92  -1.84   
3     2021-02-01  601318  中国平安  79.27  79.74  78.37  79.10  79.08   0.19   
2     2021-02-02  601318  中国平安  78.18  79.45  77.95  79.28  79.27  -1.09   
1     2021-02-03  601318  中国平安  76.54  77.74  75.30  77.74  78.18  -1.64   
0     2021-02-04  601318  中国平安  79.62  80.32  77.70  78.00  76.54   3.08   

          涨跌幅      换手率        成交量         成交金额     ma5       ma30       ma60  \
3394  38.4320  34.3936  197763351   9500302911     NaN        NaN        NaN   
3393  -0.8121   7.3921   42504832   1981445189     NaN        NaN        NaN   
3392  -4.3741   7.2904   41919674   1880502808     NaN        NaN        NaN   
3391   1.9603   5.1779   29772788   1337719318     NaN        NaN        NaN   
3390   2.7182   4.9994   28746378   1317764044  46.454        NaN        NaN   
...       ...      ...        ...          ...     ...        ...        ...   
4     -2.2739   1.1722  126980032  10098743883  82.856  85.416667  86.096000   
3      0.2403   0.6692   72490144   5729483192  81.936  85.093333  86.062667   
2     -1.3750   0.9124   98836447   7742175159  80.892  84.836000  86.009000   
1     -2.0977   1.2405  134384298  10255482626  79.844  84.526000  85.900667   
0      4.0240   1.3077  141654771  11200715086  79.004  84.318667  85.814000   

          ma120  
3394        NaN  
3393        NaN  
3392        NaN  
3391        NaN  
3390        NaN  
...         ...  
4     82.371667  
3     82.389167  
2     82.408500  
1     82.422833  
0     82.427417  

[3395 rows x 17 columns]

In [230]:
q = df['成交量']
qm = df['成交金额']
x =df['date']
date = []
for i in x:
    date.append(i.__format__('%Y/%m/%d'))


In [233]:
c = (
    Line(init_opts=opts.InitOpts(width="960px", height="400px"))
    .add_xaxis(xaxis_data=date)
    .add_yaxis(
        series_name="成交量",
        y_axis=q,
#         areastyle_opts=opts.AreaStyleOpts(opacity=0.5),
        linestyle_opts=opts.LineStyleOpts(width=2, opacity=1),
        label_opts=opts.LabelOpts(is_show=False),
    )



    .set_global_opts(
        title_opts=opts.TitleOpts(
            title="成交量",
            subtitle="601318",
            pos_left="center",
            pos_top="top",
        ),
        tooltip_opts=opts.TooltipOpts(trigger="axis", axis_pointer_type="cross"),
        legend_opts=opts.LegendOpts(pos_left="left"),
        datazoom_opts=[
            opts.DataZoomOpts(range_start=0, range_end=100),
            opts.DataZoomOpts(type_="inside", range_start=0, range_end=100),
        ],
        xaxis_opts=opts.AxisOpts(type_="category", boundary_gap=False),
        yaxis_opts=opts.AxisOpts(name="Price(¥)", type_="value"),
    )
    .set_series_opts(
        markarea_opts=opts.MarkAreaOpts(
            is_silent=False,
            
            
        ),
        axisline_opts=opts.AxisLineOpts(),
    )
#     .render("rainfall.html")
)

c.render_notebook()

In [239]:
c=(
    Line(init_opts=opts.InitOpts(width="960px", height="600px"))
    .add_xaxis(xaxis_data=date)
    .add_yaxis(
        series_name="成交量",
        y_axis=q,
        areastyle_opts=opts.AreaStyleOpts(opacity=0.5),
        linestyle_opts=opts.LineStyleOpts(),
        label_opts=opts.LabelOpts(is_show=False),
    )
    .add_yaxis(
        series_name="成交金额",
        y_axis=qm,
        yaxis_index=1,
        areastyle_opts=opts.AreaStyleOpts(opacity=0.5),
        linestyle_opts=opts.LineStyleOpts(),
        label_opts=opts.LabelOpts(is_show=False),
    )
    .extend_axis(
        yaxis=opts.AxisOpts(
            name="成交金额（¥）",
            name_location="start",
            type_="value",
#             max_=5,
            is_inverse=True,
            axistick_opts=opts.AxisTickOpts(is_show=True),
            splitline_opts=opts.SplitLineOpts(is_show=True),
        )
    )
    .set_global_opts(
        title_opts=opts.TitleOpts(
            title="成交量成交金额关系图",
            subtitle="601318",
            pos_left="center",
            pos_top="top",
        ),
        tooltip_opts=opts.TooltipOpts(trigger="axis", axis_pointer_type="cross"),
        legend_opts=opts.LegendOpts(pos_left="left"),
        datazoom_opts=[
            opts.DataZoomOpts(range_start=0, range_end=100),
            opts.DataZoomOpts(type_="inside", range_start=0, range_end=100),
        ],
        xaxis_opts=opts.AxisOpts(type_="category", boundary_gap=False),
        yaxis_opts=opts.AxisOpts(name="成交量", type_="value"),
    )
    .set_series_opts(
        markarea_opts=opts.MarkAreaOpts(
            is_silent=False,
            data=[
                opts.MarkAreaItem(
                    name="成交量",
                    x=("2009/9/12-7:00", "2009/9/22-7:00"),
                    label_opts=opts.LabelOpts(is_show=False),
                    itemstyle_opts=opts.ItemStyleOpts(color="#DCA3A2", opacity=0.5),
                ),
                opts.MarkAreaItem(
                    name="成交金额",
                    x=("2009/9/10-7:00", "2009/9/20-7:00"),
                    label_opts=opts.LabelOpts(is_show=False),
                    itemstyle_opts=opts.ItemStyleOpts(color="#A1A9AF", opacity=0.5),
                ),
            ],
        ),
        axisline_opts=opts.AxisLineOpts(),
    )
#     .render("rainfall.html")
)

c.render_notebook()